# Week 8 - Machine Learning on Point Clouds

Thus far we have only dealt with tabular data. But data comes in a huge variety of shapes and sizes.
Today we will look into applying ML on a Point Cloud.

This is ripped from the publication Grilli and Remondino, 2020 https://doi.org/10.3390/ijgi9060379

The associated GitHub Repo is https://github.com/3DOM-FBK/RF4PCC

The point cloud data we are using is from the Basilica di Paestum, Italy (Temple of Hera). It's available on Moodle.

## Let's first read in a point cloud

In [ ]:
import pandas as pd
data = pd.read_csv('./HeraTemple.txt', header=None, sep=' ')

In [126]:
data.head()

0        1        2
0 -5.03831 -6.58809 -1.29036
1 -5.01734 -6.31677 -1.21587
2 -5.01422 -6.33735 -1.26792
3 -5.01145 -6.52628 -1.28176
4 -5.01130 -6.06792 -1.28515

In [124]:
len(data)

821494

## Why not visualize the temple?

Matplotlib is not designed for huge point clouds

But we can use plotly instead. It can handle up to roughly a few hundred thousand points

In [ ]:
import plotly.graph_objects as go

In [135]:
# 800000 points is likely too many. This handy command downsamples by 5 (takes every 5th point) for the sake of plotting:
data_reduced = data.iloc[::5,:]

fig = go.Figure(data=[go.Scatter3d(
    x=data_reduced[0],
    y=data_reduced[1],
    z=data_reduced[2],
    mode='markers',
    marker=dict(
        size=2,
        color=data_reduced[2],  # Here we make the color of the point be the z coordinate. This is unnecessary, but makes it a bit easier to see
        colorscale='Viridis',
        opacity=0.8
        )
    )]
    )

fig.update_layout(title={"text":'Temple of Hera'}, autosize=True)

fig.show()

## So we have all these x,y,z points. But we need some features that an ML model can learn from!

* Radiometric Features: With RGB values we can use these (colour, lightness, etc.). Unfortunately we have no RGB values here.

* Geometric/Covariance Features: aspects of the "shape" of the region immediately surrounding point. **Note** that for these features we need to define the radius we are considering.

* Regional embeddings: We can use another ML to learn to create powerful features on its own (called "embeddings"). We will see more of this next semester!

## Let's make some Geometric Features!

These are made using 3 special values called "eigenvalues" $$(\lambda_1, \lambda_2, \lambda_3)$$

Here we will create the following three features:

* Planarity (how flat is the region) $$\frac{\lambda_2 - \lambda_3}{\lambda_1}$$

* Surface Variation (kind of self explanitory) $$\frac{\lambda_3}{\sum{\lambda}}$$

* Omnivarience (is point density high or low in all directions?) $$\sqrt[3]{\prod{\lambda}}$$

In [137]:

# First let's switch to numpy as we will be doing lots of math
import numpy as np
xyz = data.to_numpy()

# Let's try to get these three features for only the first point (xyz[0])
# We first need to find all points that are not too far away
# Let's first calculate the distances between the first point and all others
distances = [np.linalg.norm(xyz[0] - row_j) for row_j in xyz]
# Now let's choose all points in xyz that are less than 1 metre away
a = xyz[[distance < 1 for distance in distances], :]
# The following two lines find the eigenvalues for this region
cov = np.cov(a, rowvar=False)
lambda_1, lambda_2, lambda_3 = np.linalg.eigvals(cov)

# Now we can calculate the three values!
P_lambda = (lambda_2 - lambda_3)/lambda_1
O_lambda = (lambda_1*lambda_2*lambda_3)**(1/3)
C_lambda = lambda_3/(lambda_1+lambda_2+lambda_3)
print(P_lambda, O_lambda, C_lambda)


0.4773553773186933 0.013942975256446897 0.0001330154235380748


In [ ]:
# We could try to loop over all 800000 points, but it's slooooooowwwwwww

features = []

counter = 0
for row_i in xyz:
    print("Currently processing row " + str(counter))
    distances = [np.linalg.norm(row_i - row_j) for row_j in xyz]
    a = xyz[[distance < 1 for distance in distances], :]
    cov = np.cov(a, rowvar=False)
    lambda_1, lambda_2, lambda_3 = np.linalg.eigvals(cov)

    P_lambda = (lambda_2 - lambda_3)/lambda_1
    O_lambda = (lambda_1*lambda_2*lambda_3)**(1/3)
    C_lambda = lambda_3/(lambda_1+lambda_2+lambda_3)

    features.append((P_lambda, O_lambda, C_lambda))

    counter += 1

## How to speedup?

There are many ways of increasing the efficiency of the code, but in the end it really doesn't make sense to reinvent the wheel.

CloudCompute already has hyper-efficient built in systems (designed in c++ I think) to calculate these values for all points.

So we can output the data and move it there.

In [ ]:
%pip install pyntcloud

In [140]:
from pyntcloud import PyntCloud

# This convention is needed to switch the file to a point cloud
data = data.rename(columns={0:'x', 1:'y', 2:'z'})

cloud = PyntCloud(data)

cloud.to_file('HeraTemple.ply')

c:\Users\re72fam\AppData\Local\Programs\Python\Python313\Lib\site-packages\pyntcloud\io\ply.py:260: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

c:\Users\re72fam\AppData\Local\Programs\Python\Python313\Lib\site-packages\pyntcloud\io\ply.py:260: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

c:\Users\re72fam\AppData\Local\Programs\Python\Python313\Lib\site-packages\pyntcloud\io\ply.py:260: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

## What comes next?

In CloudCompare we can now:

1) Read in the .ply file.
2) Select the "HeraTemple - Cloud" item from the DB Tree list on the left
3) Go to "Tools" >> "Other" >> "Geometric Features"
4) Set the Radius and create the desired scalar features
5) Save the file with the features as an ASCII cloud (.txt file)

We can also annotate a section for training purposes. To do this:
1) Click on the scissors in the middle of the top toolbar (segment)
2) Choose a region with left clicks, then right click to close it
3) Click on "Segment Out" in the toolbar that has appeared in the top right (the 5th button)
4) Click on the Green Checkmark on the same toolbar
5) In the DB tree on the left select only the part you segmented out
6) Click on the "+" sign on the top toolbar (add constant SF)
7) Give the feature a name and a value (ie. buttress, 1)
8) Save the file with the annotated labels as an ASCII cloud (.txt file)

## And now for the ML stuff!

We can now bring in our new annotated file. To save the trouble of tedious annotating, bring in the TRAINING.txt file. It has both features and class labels, and can be found here:
./TRAINING.txt

In [ ]:
data_annotated = pd.read_csv('./TRAINING.txt', header=None, sep=' ')

In [ ]:
# Note that the features (columns 3-9) have been normalized with basic 0-1 normalization
data_annotated.head()

0        1        2         3         4         5         6   \
0 -9.79163 -5.94998 -2.03110  0.842597  0.498449  0.024359  0.018015   
1 -9.77569 -5.73259 -2.07183  0.872824  0.638744  0.024420  0.018667   
2 -9.77369 -5.83082 -2.06892  0.828149  0.619036  0.024992  0.018611   
3 -9.77140 -6.00107 -1.91309  0.636605  0.312037  0.023442  0.016555   
4 -9.77042 -5.97178 -1.96992  0.800627  0.373881  0.024109  0.017266   

         7         8        9    10  
0  0.992240  0.313641 -2.03110  0.0  
1  0.992049  0.295047 -2.07183  0.0  
2  0.992164  0.300611 -2.06892  0.0  
3  0.992596  0.349482 -1.91309  0.0  
4  0.992419  0.341006 -1.96992  0.0

In [147]:
fig = go.Figure(data=[go.Scatter3d(
    x=data_annotated[0],
    y=data_annotated[1],
    z=data_annotated[2],
    mode='markers',
    marker=dict(
        size=2,
        color=data_annotated[10],  # We colour the model based on the class labels
        colorscale='Viridis',
        opacity=0.8
        )
    )]
    )

fig.update_layout(title={"text":'Annotated Column'}, autosize=True)

fig.show()

# Exercise

You will now be training a Random Forest Classifier on this single column and using it to predict the classes for the entire temple!

Here are the steps you should follow:

1) Split this data for a single column into X_train (all features) and Y_train (the classes). "iloc" will be useful here

2) Import the RandomForestClassifier from sklearn.ensemble. Fit it to the train data

3) Read in the full temple WITH geometric features, which is the TEST.txt file available here: https://drive.google.com/drive/folders/1AAUKtw_m35L_LQshM644xxo_4auav9Vq?usp=sharing

4) From this, remove the first 3 columns (x,y,z) so you have only the features, and save this as X_test

5) Use your RandomFOrestClassifier (which has already been fit to the train data) to generate class predictions. Save these as "preds"

6) Attach these preds as a new column to the full temple dataframe (which still has the x,y,z columns)

7) Plot the full temple dataframe, with the colour set to be the new "preds" column you added. Don't forget to downsample first

8) Admire your work!

## Let's split the data into X_train and Y_train

In [161]:
X_train = data_annotated.iloc[:, 3:10]
Y_train = data_annotated.iloc[:,-1]

In [158]:
X_train.head()

3         4         5         6         7         8        9
0  0.842597  0.498449  0.024359  0.018015  0.992240  0.313641 -2.03110
1  0.872824  0.638744  0.024420  0.018667  0.992049  0.295047 -2.07183
2  0.828149  0.619036  0.024992  0.018611  0.992164  0.300611 -2.06892
3  0.636605  0.312037  0.023442  0.016555  0.992596  0.349482 -1.91309
4  0.800627  0.373881  0.024109  0.017266  0.992419  0.341006 -1.96992

In [162]:
Y_train.head()

0    0.0
1    0.0
2    0.0
3    0.0
4    0.0
Name: 10, dtype: float64

## Fitting our Random Forest Classifier to the Training Data

In [196]:
from sklearn.ensemble import RandomForestClassifier

RFC = RandomForestClassifier(random_state=0, oob_score=True)  # The oob_score is not required, but helps us get a bit more performance when we don't have a way to actually test the predicted labels

RFC.fit(X_train, Y_train)

RandomForestClassifier(oob_score=True, random_state=0)

## Bring in the Full Temple Data With Geometrical Features (Test.txt)

In [ ]:
full_data = pd.read_csv('./TEST.txt', header=None, sep=' ')
X_test = full_data.iloc[:,3::]

In [174]:
X_test.head()

3         4         5         6         7         8        9
0  0.000820  0.000921  0.000519  0.000267  0.999741  0.970962 -1.29036
1  0.000226  0.000355  0.000527  0.000268  0.999692  0.989392 -1.21587
2  0.000283  0.000387  0.000532  0.000272  0.999695  0.992515 -1.26792
3  0.001293  0.000784  0.000516  0.000267  0.999733  0.975968 -1.28176
4  0.000370  0.000338  0.000810  0.000417  0.999644  0.980715 -1.28515

## Create Predictions for the Classes

In [175]:
preds = RFC.predict(X_test)

In [ ]:
# Add a 10th column containing these class label predictions
full_data[10] = preds

## Viewing the Final Result

In [197]:
# Now we plot everything (don't forget to downsample)
full_data = full_data.iloc[::5,:]

fig = go.Figure(data=[go.Scatter3d(
    x=full_data[0],
    y=full_data[1],
    z=full_data[2],
    mode='markers',
    marker=dict(
        size=2,
        color=full_data[10],  # We colour the model based on the class labels
        colorscale='Viridis',
        opacity=0.8
        )
    )]
    )

fig.update_layout(title={"text":'Temple of Hera'}, autosize=True)

fig.show()